In [2]:
import json
import pandas as pd
import jieba
from jieba import posseg
import numpy as np
from loader import *
import pickle
import torch
from torch import nn
from torch.nn import functional as F
import random
import sys
# from modules import embedding, encoder, model_sbj
from sklearn.model_selection import KFold

In [3]:
file_path = '../data/train_data.json'

In [8]:
def gen_train_data_ner(file_path):
    texts = []
    char_lists = []
    spo_lists = []
    with open(file_path, 'r') as f:
        for line in f:
            tmp = json.loads(line)
            text = tmp['text'].lower().strip()
            texts.append(text)
            char_list = split_word(text)
            char_lists.append(char_list)
            spo_lists.append(tmp['spo_list'])

    r_texts = []
    r_char_lists = []
    r_ners = []
    for text, char_list, spo_list in zip(texts, char_lists, spo_lists):
        char_len = len(char_list)
        ner = np.zeros(char_len)

        spo_extract = set()
        sbj_set = set([spo['subject'].lower().strip() for spo in spo_list])
        obj_set = set([spo['object'].lower().strip() for spo in spo_list])
        ner_set = sbj_set | obj_set
        ner_set = list(ner_set)
        np.random.shuffle(ner_set)
        
        xxxx = False
        for ner_i in ner_set:
            nums = 0
            ner_list = split_word(ner_i)
            ner_len = len(ner_list)
            for i in range(0, char_len-ner_len+1):
                if char_list[i: i+ner_len] == ner_list:
                    ner_s = i
                    ner_e = i + ner_len - 1
                    
                    nums += 1
                    

#                     flag = False
#                     for item in ner[ner_s: ner_e+1]:
#                         if item != 0:
#                             flag = True
#                             break
#                     if flag:
#                         continue

                    if ner_s == ner_e:
                        ner[ner_s] = 4
                    elif ner_e - ner_s == 1:
                        ner[ner_s] = 1
                        ner[ner_e] = 3
                    elif ner_e - ner_s > 1:
                        ner[ner_s] = 1
                        ner[ner_s+1: ner_e] = 2
                        ner[ner_e] = 3
                    else:
                        print('wrong')
                        assert 1 == -1
                    spo_extract.add(ner_i)
            if nums > 1:
                xxxx = True
        
        if xxxx:
            print(text)
            print('sbj:',sbj_set)
            print('obj:', obj_set)
            print('spo:', spo_list)
            print('')

        if len(spo_extract) != 0:
            r_texts.append(text)
            r_char_lists.append(char_list)
            r_ners.append(ner.tolist())

    print('ner, make samples_num:%d/%d, radio:%.4f' % (len(r_texts), len(texts), len(r_texts)/len(texts)))

    return r_char_lists, r_ners

In [9]:
a = gen_train_data_ner(file_path)

如何演好自己的角色，请读《演员自我修养》《喜剧之王》周星驰崛起于穷困潦倒之中的独门秘笈
sbj: {'喜剧之王'}
obj: {'周星驰'}
spo: [{'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '周星驰', 'subject': '喜剧之王'}]

茶树茶网蝽，stephanitis chinensis drake，属半翅目网蝽科冠网椿属的一种昆虫
sbj: {'茶树茶网蝽'}
obj: {'半翅目'}
spo: [{'predicate': '目', 'object_type': '目', 'subject_type': '生物', 'object': '半翅目', 'subject': '茶树茶网蝽'}]

丝角蝗科，oedipodidae，昆虫纲直翅目蝗总科的一个科
sbj: {'丝角蝗科'}
obj: {'直翅目'}
spo: [{'predicate': '目', 'object_type': '目', 'subject_type': '生物', 'object': '直翅目', 'subject': '丝角蝗科'}]

爱德华·尼科·埃尔南迪斯（1986-），是一位身高只有70公分哥伦比亚男子，体重10公斤，只比随身行李高一些，2010年获吉尼斯世界纪录正式认证，成为全球当今最矮的成年男人
sbj: {'爱德华·尼科·埃尔南迪斯'}
obj: {'70公分', '1986', '哥伦比亚'}
spo: [{'predicate': '身高', 'object_type': 'Number', 'subject_type': '人物', 'object': '70公分', 'subject': '爱德华·尼科·埃尔南迪斯'}, {'predicate': '出生日期', 'object_type': 'Date', 'subject_type': '人物', 'object': '1986', 'subject': '爱德华·尼科·埃尔南迪斯'}, {'predicate': '国籍', 'object_type': '国家', 'subject_type': '人物', 'object': '哥伦比亚', 'subject': '爱德华·尼科·埃


桥亭活鱼小镇始创于1999年11月18日1，福建省著名商标，以直营和合伙联营为发展模式的现代餐饮企业，公司前身为“聚全兴水煮活鱼馆”，经过十四年的发展，现已拥有福州、厦门、武夷山、三明、泉州等多个区域50家直营店
sbj: {'桥亭活鱼小镇'}
obj: {'1999年11月18日'}
spo: [{'predicate': '成立日期', 'object_type': 'Date', 'subject_type': '机构', 'object': '1999年11月18日', 'subject': '桥亭活鱼小镇'}]

婚誓作词:于彦夫雷振邦作曲:雷振邦演唱:黄莉媛lrc编辑:毓杰(吉林延边)阿哥阿妹的情意长好象那流水日夜响流水也会有时尽阿哥永远在我身旁阿哥阿妹的情意深好象那芭蕉一条根阿哥好比那芭蕉叶阿妹就是那芭蕉心(music)lrc编辑:毓杰燕子双双飞上天我和阿哥打秋千秋千荡到晴空里好象燕子云里穿鲜花开放蜜蜂来鲜花蜜蜂分不开蜜蜂生来就恋鲜花恋鲜花为着你放开lrc编辑:毓杰(吉林延边)1
sbj: {'婚誓'}
obj: {'雷振邦'}
spo: [{'predicate': '作词', 'object_type': '人物', 'subject_type': '歌曲', 'object': '雷振邦', 'subject': '婚誓'}]

《穿越神雕侠侣之杨过》是连载于起点中文网的同人小说，作者是神帝的大鹏
sbj: {'穿越神雕侠侣之杨过'}
obj: {'神帝的大鹏'}
spo: [{'predicate': '作者', 'object_type': '人物', 'subject_type': '图书作品', 'object': '神帝的大鹏', 'subject': '穿越神雕侠侣之杨过'}]

《海》是王梵瑞的音乐作品，收录在《青春》专辑中
sbj: {'海'}
obj: {'王梵瑞', '《青春》'}
spo: [{'predicate': '所属专辑', 'object_type': '音乐专辑', 'subject_type': '歌曲', 'object': '《青春》', 'subject': '海'}, {'predicate': '歌手', 'object_type': '人物', 'subject_type': '歌曲', 'ob

sbj: {'尖齿紫晶报春（亚种）'}
obj: {'报春花目'}
spo: [{'predicate': '目', 'object_type': '目', 'subject_type': '生物', 'object': '报春花目', 'subject': '尖齿紫晶报春（亚种）'}]

在粉丝们强烈的热情下，蒋雪儿又接连献唱了《回不去》、《梦的翅膀受了伤》、《真的好可惜》等热门曲目
sbj: {'回不去', '梦的翅膀受了伤'}
obj: {'蒋雪儿'}
spo: [{'predicate': '歌手', 'object_type': '人物', 'subject_type': '歌曲', 'object': '蒋雪儿', 'subject': '梦的翅膀受了伤'}, {'predicate': '歌手', 'object_type': '人物', 'subject_type': '歌曲', 'object': '蒋雪儿', 'subject': '回不去'}]

《中国经济指南》是2016年由清华大学出版社出版的图书，作者是邹至庄、dwight heald perkins
sbj: {'中国经济指南'}
obj: {'清华大学出版社', '邹至庄'}
spo: [{'predicate': '出版社', 'object_type': '出版社', 'subject_type': '书籍', 'object': '清华大学出版社', 'subject': '中国经济指南'}, {'predicate': '作者', 'object_type': '人物', 'subject_type': '图书作品', 'object': '邹至庄', 'subject': '中国经济指南'}]

《中国故事》由斯琴高娃、高曙光、李雪健主演于2005上映的电视剧
sbj: {'中国故事'}
obj: {'斯琴高娃', '李雪健', '2005', '高曙光'}
spo: [{'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '斯琴高娃', 'subject': '中国故事'}, {'predicate': '主演', 'object_type': '人物', 'subject_ty

obj: {'吴敬梓'}
spo: [{'predicate': '作者', 'object_type': '人物', 'subject_type': '图书作品', 'object': '吴敬梓', 'subject': '儒林外史'}]

冯绍峰最帅的4个角色：卡索 冯绍峰在古装玄幻剧《幻城》中饰演重情重义的冰族王子卡索，是万年来幻术资质最高的神，拥有比上古先祖还强大的灵力
sbj: {'幻城'}
obj: {'冯绍峰'}
spo: [{'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '冯绍峰', 'subject': '幻城'}]

《最后一个男人》是由菲尔·罗德执导的电视剧，威尔·福特等参加演出，于2015年3月1日在美国上映，讲述了在未来的某一天，地球上除了phil miller，没有了别人的故事
sbj: {'最后一个男人'}
obj: {'2015年3月1日', '菲尔·罗德', '威尔·福特'}
spo: [{'predicate': '导演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '菲尔·罗德', 'subject': '最后一个男人'}, {'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '威尔·福特', 'subject': '最后一个男人'}, {'predicate': '上映时间', 'object_type': 'Date', 'subject_type': '影视作品', 'object': '2015年3月1日', 'subject': '最后一个男人'}]

韩雪从小就是品学兼优的好学生，临近高考还利用暑假和两个月的课时接连拍摄了电影《浪漫樱花》和连续剧《南北一家亲》，尽管如此她依然考了500多分，成了2000年上海戏剧学院文化考试的第一名
sbj: {'韩雪', '南北一家亲'}
obj: {'上海戏剧学院', '韩雪'}
spo: [{'predicate': '毕业院校', 'object_type': '学校', 'subject_type': '人物'

《王铎书法精选》是2006年河南美术出版社出版的图书，作者是刘灿章
sbj: {'王铎书法精选'}
obj: {'刘灿章', '河南美术出版社'}
spo: [{'predicate': '作者', 'object_type': '人物', 'subject_type': '图书作品', 'object': '刘灿章', 'subject': '王铎书法精选'}, {'predicate': '出版社', 'object_type': '出版社', 'subject_type': '书籍', 'object': '河南美术出版社', 'subject': '王铎书法精选'}]

《风雨中的爱情》是新月光创作的网络小说，发表于17k小说网
sbj: {'风雨中的爱情'}
obj: {'新月光', '17k小说网'}
spo: [{'predicate': '连载网站', 'object_type': '网站', 'subject_type': '网络小说', 'object': '17K小说网', 'subject': '风雨中的爱情'}, {'predicate': '作者', 'object_type': '人物', 'subject_type': '图书作品', 'object': '新月光', 'subject': '风雨中的爱情'}]

因主演张艺谋执导电影《山楂树之恋》被观众熟知，郑爽，1991年8月22日出生于辽宁省沈阳市，毕业于北京电影学院，中国内地影视女演员
sbj: {'郑爽', '山楂树之恋'}
obj: {'中国', '张艺谋', '1991年8月22日', '辽宁省沈阳市', '北京电影学院'}
spo: [{'predicate': '毕业院校', 'object_type': '学校', 'subject_type': '人物', 'object': '北京电影学院', 'subject': '郑爽'}, {'predicate': '出生日期', 'object_type': 'Date', 'subject_type': '人物', 'object': '1991年8月22日', 'subject': '郑爽'}, {'predicate': '国籍', 'object_type': '国家', 'subject_type': '人物

...

夏文汐复出的首部作品，将接拍由名作词人潘源良执导的电影《出轨的女人》，戏中陈伟霆将会饰演一名男妓，周旋于以夏文汐为首的三名女性当中，戏中不乏意识大胆的情欲场面
sbj: {'出轨的女人'}
obj: {'潘源良', '夏文汐'}
spo: [{'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '夏文汐', 'subject': '出轨的女人'}, {'predicate': '导演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '潘源良', 'subject': '出轨的女人'}]

个人简历籍贯焦佩武 男，汉族，1928年1月生，安徽蒙城人
sbj: {'焦佩武'}
obj: {'安徽蒙城', '1928年1月', '汉族'}
spo: [{'predicate': '民族', 'object_type': 'Text', 'subject_type': '人物', 'object': '汉族', 'subject': '焦佩武'}, {'predicate': '出生地', 'object_type': '地点', 'subject_type': '人物', 'object': '安徽蒙城', 'subject': '焦佩武'}, {'predicate': '出生日期', 'object_type': 'Date', 'subject_type': '人物', 'object': '1928年1月', 'subject': '焦佩武'}]

2015年11月13日，陈妍希主演的青春爱情片《年少轻狂》上映，她在片中饰演乖巧可爱、性格腼腆的女主角邱樱子，并献唱个人创作的电影插曲《哗啦啦》24825
sbj: {'年少轻狂'}
obj: {'2015年11月13日', '陈妍希'}
spo: [{'predicate': '上映时间', 'object_type': 'Date', 'subject_type': '影视作品', 'object': '2015年11月13日', 'subject': '年少轻狂'}, {'predicate': '主演', 'object_type': '人物', 's

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.




《我来接您了》是日本电视台（ntv）2016年制作播出的电视连续剧，由南云圣一、冢本连平、小室直子执导，尾崎将也、泉泽阳子编剧，福士苍汰主演，土屋太凤、铃木亮平等出演，于2016年4月23日首播
sbj: {'我来接您了'}
obj: {'小室直子', '尾崎将也', '泉泽阳子', '南云圣一', '冢本连平', '福士苍汰', 'ntv'}
spo: [{'predicate': '编剧', 'object_type': '人物', 'subject_type': '影视作品', 'object': '泉泽阳子', 'subject': '我来接您了'}, {'predicate': '主演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '福士苍汰', 'subject': '我来接您了'}, {'predicate': '出品公司', 'object_type': '企业', 'subject_type': '影视作品', 'object': 'NTV', 'subject': '我来接您了'}, {'predicate': '导演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '冢本连平', 'subject': '我来接您了'}, {'predicate': '导演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '小室直子', 'subject': '我来接您了'}, {'predicate': '编剧', 'object_type': '人物', 'subject_type': '影视作品', 'object': '尾崎将也', 'subject': '我来接您了'}, {'predicate': '导演', 'object_type': '人物', 'subject_type': '影视作品', 'object': '南云圣一', 'subject': '我来接您了'}]

人物生平早年经历周虓（《资治通鉴》作周飏1），字孟威，祖籍汝南安城，是安南将军周访玄孙，镇西将军周抚曾孙，冠军将军周楚之孙，东羌校尉周琼之子
sbj: {'周虓'}
obj: 

spo: [{'predicate': '目', 'object_type': '目', 'subject_type': '生物', 'object': '新腹足目', 'subject': '雷娜特芋螺'}]

周炳吉，著名战略策划人，教授，笔名双喆，山东琅琊人，现任中国企业策划师协会的会长、鸿吉企程营销策划有限公司董事长、中国十大战略策划人并兼任中华孝道基金会秘书长、中国农业化肥产业协会秘书长，担任大连策划师大学组委会主任、大连策划师大学副校长
sbj: {'周炳吉'}
obj: {'山东琅琊人'}
spo: [{'predicate': '祖籍', 'object_type': '地点', 'subject_type': '人物', 'object': '山东琅琊人', 'subject': '周炳吉'}]

明朝和清朝，都有着两百多年的统治，当时明朝开国皇帝朱元璋，带兵攻打元军，建立了属于自己的朝代，明朝
sbj: {'朱元璋'}
obj: {'明朝'}
spo: [{'predicate': '朝代', 'object_type': 'Text', 'subject_type': '历史人物', 'object': '明朝', 'subject': '朱元璋'}]

《现代僵尸的奇异生活》是一部在17k小说网连载的玄幻小说，作者是月光红颜
sbj: {'现代僵尸的奇异生活'}
obj: {'月光红颜', '17k小说网'}
spo: [{'predicate': '连载网站', 'object_type': '网站', 'subject_type': '网络小说', 'object': '17k小说网', 'subject': '现代僵尸的奇异生活'}, {'predicate': '作者', 'object_type': '人物', 'subject_type': '图书作品', 'object': '月光红颜', 'subject': '现代僵尸的奇异生活'}]

《帝恨天》是哈尼哈尼创作的网络小说，发表于17k小说网
sbj: {'帝恨天'}
obj: {'哈尼哈尼', '17k小说网'}
spo: [{'predicate': '作者', 'object_type': '人物', 'subject_type': '图书作品', 'object': 

KeyboardInterrupt: 

In [21]:
b = torch.nn.Parameter(torch.Tensor(a))
b.requires_grad = False

In [24]:
F.linear(b, b)

tensor([[1., 0.],
        [0., 1.]])

In [2]:
file_path = '../data/train_data.json'

In [3]:
a = gen_train_data_join(file_path)

p, making sample_num:169262/173108, radio:0.9778


6

In [5]:
with open('../data/obj_dict.pkl', 'rb') as f:
        obj2i = pickle.load(f)['obj2i']

In [9]:
with open('../data/sbj_dict.pkl', 'rb') as f:
        sbj2i = pickle.load(f)['sbj2i']

In [13]:
len(sbj2i.keys() | obj2i.keys())

28

In [10]:
set(sbj2i.keys())

{'书籍',
 '人物',
 '企业',
 '历史人物',
 '国家',
 '图书作品',
 '地点',
 '学科专业',
 '影视作品',
 '景点',
 '机构',
 '歌曲',
 '生物',
 '电视综艺',
 '网络小说',
 '行政区'}

In [8]:
set(obj2i.keys())

{'Date',
 'Number',
 'Text',
 '人物',
 '企业',
 '作品',
 '出版社',
 '国家',
 '地点',
 '城市',
 '学校',
 '气候',
 '目',
 '网站',
 '语言',
 '音乐专辑'}

In [8]:
list(p2i.keys())

['语言',
 'Text',
 '人物',
 '气候',
 '地点',
 'Number',
 '企业',
 '作品',
 '学校',
 '出版社',
 '网站',
 '城市',
 '音乐专辑',
 'Date',
 '目',
 '国家']